In [ ]:
import pandas as pd
import numpy as np

In [ ]:
from google.colab import files
uploaded = files.upload()

Saving games.csv to games (1).csv


In [ ]:
games=pd.read_csv("games.csv", encoding="latin-1")

# Parte 1: Procesamiento de los datos

## *Análisis de las características*

Observamos los datos que tenemos para poder analizar que columnas tienen influencia en cada vector de clase

In [ ]:
games.dtypes

NameError: ignored

Eliminamos los datos que concluimos que no aportaban a la predicción de las clases correspondientes para cada caso

In [ ]:
#editora = vector de clase: Publisher
editora=games.copy()
editora=editora.drop(['Id','Year','Difficulty'],axis=1)

In [ ]:
#otrasventas = vector de clase: Other_sales
otrasventas=games.copy()
otrasventas=otrasventas.drop(['Id','Difficulty','Year'],axis=1)
otrasventas=otrasventas.dropna(subset=['Other_Sales'])

## *Limpiar valores nulos*

https://www.geeksforgeeks.org/python-pandas-series-isnull/

Primero revisamos cuantos datos nulos tiene cada atributo

In [ ]:
print("cantidad de valores nulos para el atributo 'Ign_score': ",sum(pd.isnull(games['Ign_score'])))
print("cantidad de valores nulos para el atributo 'Rank': ",sum(pd.isnull(games['Rank'])))
print("cantidad de valores nulos para el atributo 'Platform': ",sum(pd.isnull(games['Platform'])))
print("cantidad de valores nulos para el atributo 'Year': ",sum(pd.isnull(games['Year'])))
print("cantidad de valores nulos para el atributo 'Genre': ",sum(pd.isnull(games['Genre'])))
print("cantidad de valores nulos para el atributo 'Publisher': ",sum(pd.isnull(games['Publisher'])))
print("cantidad de valores nulos para el atributo 'NA_Sales': ",sum(pd.isnull(games['NA_Sales'])))
print("cantidad de valores nulos para el atributo 'EU_Sales': ",sum(pd.isnull(games['EU_Sales'])))
print("cantidad de valores nulos para el atributo 'JP_Sales': ",sum(pd.isnull(games['JP_Sales'])))
print("cantidad de valores nulos para el atributo 'Other_Sales': ",sum(pd.isnull(games['Other_Sales'])))

A partir de la cantidad de valores nulos de 'Ign_score' decidimos eliminar esta columna para ambos casos

In [ ]:
editora=editora.drop(['Ign_score'],axis=1)
otrasventas=otrasventas.drop(['Ign_score'],axis=1)

https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.fillna.html

Para el resto de los casos númericos decidimos rellenar los datos faltantes con el promedio de los datos

In [ ]:
editora['NA_Sales']=editora['NA_Sales'].fillna(editora['NA_Sales'].mean())
editora['EU_Sales']=editora['EU_Sales'].fillna(editora['EU_Sales'].mean())
editora['JP_Sales']=editora['JP_Sales'].fillna(editora['JP_Sales'].mean())
editora['Other_Sales']=editora['Other_Sales'].fillna(editora['Other_Sales'].mean())

In [ ]:
otrasventas['NA_Sales']=otrasventas['NA_Sales'].fillna(otrasventas['NA_Sales'].mean())
otrasventas['EU_Sales']=otrasventas['EU_Sales'].fillna(otrasventas['EU_Sales'].mean())
otrasventas['JP_Sales']=otrasventas['JP_Sales'].fillna(otrasventas['JP_Sales'].mean())
otrasventas['Other_Sales']=otrasventas['Other_Sales'].fillna(otrasventas['Other_Sales'].mean())

https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.dropna.html

Para los datos no numéricos decidimos eliminar las filas donde estos valores fueran nulos

In [ ]:
editora=editora.dropna(subset=['Publisher']).reset_index(drop=True)
editora=editora.dropna(subset=['Platform']).reset_index(drop=True)
editora=editora.dropna(subset=['Genre']).reset_index(drop=True)
editora=editora.dropna(subset=['Name']).reset_index(drop=True)

In [ ]:
otrasventas=otrasventas.dropna(subset=['Publisher']).reset_index(drop=True)
otrasventas=otrasventas.dropna(subset=['Genre']).reset_index(drop=True)
otrasventas=otrasventas.dropna(subset=['Platform']).reset_index(drop=True)
otrasventas=otrasventas.dropna(subset=['Name']).reset_index(drop=True)

## *Separar la clase y normalizar*

Separamos cada caso en un vector de clases y una matriz de características (features)

In [ ]:
clase_editora=editora[['Publisher']]
features_editora=editora.drop(['Publisher'], axis=1)
clase_otrasventas=otrasventas[['Other_Sales']]
features_otrasventas=otrasventas.drop(['Other_Sales'], axis=1)

In [ ]:
!pip install sklearn


https://scikit-learn.org/stable/modules/generated/sklearn.preprocessing.LabelEncoder.html

Encodeamos para despues poder normalizar todo el dataframe de features

In [ ]:
from sklearn import preprocessing
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
features_otrasventas["Platform"]=le.fit_transform(features_otrasventas["Platform"])
features_otrasventas["Genre"]=le.fit_transform(features_otrasventas["Genre"])
features_otrasventas["Publisher"]=le.fit_transform(features_otrasventas["Publisher"])
features_otrasventas['Name']=le.fit_transform(features_otrasventas['Name'])
features_editora['Platform']=le.fit_transform(features_editora['Platform'])
features_editora['Genre']=le.fit_transform(features_editora['Genre'])
features_editora['Name']=le.fit_transform(features_editora['Name'])
clase_editora['Publisher']=le.fit_transform(clase_editora['Publisher'])

https://stackoverflow.com/questions/26414913/normalize-columns-of-pandas-data-frame

Ahora normalizamos las features

In [ ]:
from sklearn.preprocessing import MinMaxScaler

scaler = MinMaxScaler()
scaled_values_1 = scaler.fit_transform(features_editora)
features_editora.loc[:,:] = scaled_values_1
scaled_values_2 = scaler.fit_transform(features_otrasventas)
features_otrasventas.loc[:,:] = scaled_values_2

# Parte 2: Clasificación automática y regresión

## *Separar datos de entrenamiento y pruebas*

In [ ]:
from sklearn import neighbors
from sklearn import metrics
from sklearn.model_selection import train_test_split

In [ ]:
y=clase_editora
X=features_editora
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3001, random_state=3)

Repetimos para el otro caso

In [ ]:
y2=clase_otrasventas
X2=features_otrasventas
X2_train, X2_test, y2_train, y2_test = train_test_split(X2, y2, test_size=0.5)


##*Instanciar y entrenar el clasificador*

Instanciamos y entramos el clasificador utilizando como clase el atributo editora del juego.

In [ ]:
knn = neighbors.KNeighborsClassifier(n_neighbors=23, weights='distance', algorithm='auto')
knn.fit(X_train, y_train)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:2: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  


KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
                     metric_params=None, n_jobs=None, n_neighbors=23, p=2,
                     weights='distance')

##*Instanciar y entrenar el regresor*

In [ ]:
from sklearn import utils, linear_model

https://scikit-learn.org/stable/auto_examples/linear_model/plot_ols.html

Creamos el regresor.

In [ ]:
regr = linear_model.LinearRegression()

Entrenamos el modelo utilizando como clase las ventas en el resto del mundo.

In [ ]:
regr.fit(X2_train, y2_train)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None, normalize=False)

##*Calcular el rendimiento del clasificador y regresor*

####-Vemos el rendimiento del clasficador

Hacemos la predicción para el primer caso utilizando el set de testeo

In [ ]:
y_pred = knn.predict(X_test)

https://scikit-learn.org/stable/modules/model_evaluation.html#classification-metrics

Vemos el rendimiento utilizando las métricas: accuracy, precision, recall y f-1 score.

In [ ]:
from sklearn.metrics import accuracy_score, f1_score, recall_score, precision_score
print("Accuracy: ",accuracy_score(y_test, y_pred))
print("F1 Score: ", f1_score(y_test, (y_pred), average='macro'))
print("Recall score: ",recall_score(y_test, (y_pred), average='macro'))
print("Precision score: ", (precision_score(y_test, (y_pred), average='macro')))


Accuracy:  0.24153908138597904
F1 Score:  0.04411570612821061
Recall score:  0.04328765915871385
Precision score:  0.05532958548063731


/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Predecimos el modelo con el set de entrenamiento

In [ ]:
y_pred2 = knn.predict(X_train)

Vemos el rendimiento utilizando las métricas: accuracy, precision, recall y f-1 score.

In [ ]:
print("Accuracy: ",accuracy_score(y_train, (y_pred2)))
print("F1 Score: ", f1_score(y_train, (y_pred2), average='macro'))
print("Recall score: ",recall_score(y_train, (y_pred2), average='macro'))
print("Precision score: ", (precision_score(y_train, (y_pred2), average='macro')))


Accuracy:  1.0
F1 Score:  1.0
Recall score:  1.0
Precision score:  1.0



####-Vemos el rendimiento del regresor

Hacemos predicciones usando el set de testeo

In [ ]:
y2_pred = regr.predict(X2_test)

https://scikit-learn.org/stable/modules/generated/sklearn.metrics.mean_squared_error.html#sklearn.metrics.mean_squared_error

Reporteamos la métrica de error i.e. mean square error

In [ ]:
from sklearn.metrics import mean_squared_error
print('Mean squared error: %.2f'
      % mean_squared_error(y2_test, y2_pred))

Mean squared error: 0.01


#Parte 3: Reducción de dimensionalidad y clustering

##*Reducción de dimensionalidad*

In [ ]:
featureseditora=editora.copy()
featureseditora=editora.drop(['Publisher'],axis=1)

In [ ]:
featureseditora['Platform']=le.fit_transform(featureseditora['Platform'])
featureseditora['Genre']=le.fit_transform(featureseditora['Genre'])
featureseditora['Name']=le.fit_transform(featureseditora['Name'])

In [ ]:
featureseditora.shape

(16540, 8)

In [ ]:
from sklearn.manifold import TSNE

https://scikit-learn.org/stable/modules/generated/sklearn.manifold.TSNE.html

Aplicamos técnica T-distributed Stochastic Neighbor Embedding (t-SNE)

In [ ]:
tsne = TSNE(n_components=2, verbose=1, perplexity=30, n_iter=300)
X_embedded = tsne.fit_transform(featureseditora)

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 16540 samples in 0.236s...
[t-SNE] Computed neighbors for 16540 samples in 0.400s...
[t-SNE] Computed conditional probabilities for sample 1000 / 16540
[t-SNE] Computed conditional probabilities for sample 2000 / 16540
[t-SNE] Computed conditional probabilities for sample 3000 / 16540
[t-SNE] Computed conditional probabilities for sample 4000 / 16540
[t-SNE] Computed conditional probabilities for sample 5000 / 16540
[t-SNE] Computed conditional probabilities for sample 6000 / 16540
[t-SNE] Computed conditional probabilities for sample 7000 / 16540
[t-SNE] Computed conditional probabilities for sample 8000 / 16540
[t-SNE] Computed conditional probabilities for sample 9000 / 16540
[t-SNE] Computed conditional probabilities for sample 10000 / 16540
[t-SNE] Computed conditional probabilities for sample 11000 / 16540
[t-SNE] Computed conditional probabilities for sample 12000 / 16540
[t-SNE] Computed conditional probabilities for sam

Vemos como nuestros datos ahora quedan representados por solo dos columnas

In [ ]:
X_embedded.shape

(16540, 2)

## *Visualizar datos reducidos*

In [ ]:
import altair as alt

In [ ]:
df_subset=pd.DataFrame(X_embedded,columns=['x','y'])
df_subset.shape

(16540, 2)

In [ ]:
featureseditora=featureseditora.join(df_subset)
featureseditora=editora[['Publisher']].join(featureseditora)
featureseditora

Publisher   Name  Platform  ...  Other_Sales          x         y
0        Nintendo  10959        26  ...         8.46   2.468442 -8.313394
1        Nintendo   9289        11  ...         0.77   4.712146 -5.956532
2        Nintendo   5549        26  ...         3.31   8.989947  3.418463
3        Nintendo  10961        26  ...         2.96   2.468707 -8.314384
4        Nintendo   7318         5  ...         1.00  10.005442 -4.778192
...           ...    ...       ...  ...          ...        ...       ...
16535       Kemco  11053         6  ...         0.00  11.029422  2.921245
16536  Infogrames   5772         7  ...         0.00   3.539544  2.298972
16537  Activision   8114        16  ...         0.00  10.350456 -2.492744
16538    7G//AMES   4991         4  ...         0.00   2.415251  3.290741
16539     Wanadoo   8934         6  ...         0.00  11.065572 -2.120314

[16540 rows x 11 columns]

https://altair-viz.github.io/user_guide/faq.html

In [ ]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

https://altair-viz.github.io/gallery/scatter_tooltips.html

In [ ]:
alt.Chart(featureseditora).mark_circle(size=60).encode(
    x='x:Q',
    y='y:Q',
    color='Publisher'
)

alt.Chart(...)

## *Predecir las clases usando clustering*

**Clustering basado en centroides**

  Preparamos Dataset:

In [ ]:
cluster_centroides=df_subset.copy()

Determinamos numero de clusters (método del codo):

https://pythonprogramminglanguage.com/kmeans-elbow-method/
https://scikit-learn.org/stable/modules/generated/sklearn.metrics.silhouette_score.html

In [ ]:
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_samples, silhouette_score
from yellowbrick.cluster import KElbowVisualizer
X=df_subset.iloc[:,:].values
#Probamos para varios valores de k

k=300
kmeanModel1 = KMeans(n_clusters=k, random_state=0)
kmeanModel1.fit(X)
print("Para k=300, la silhouette score es de:", silhouette_score(X, kmeanModel1.labels_))



Para k=300, la silhouette score es de: 0.41967043


Luego de numerosas pruebas, encontramos la silhouette score más alta al tener 300 clusters.


https://scikit-learn.org/stable/modules/generated/sklearn.cluster.KMeans.html

Predecimos la clase usando clustering

In [ ]:
kmeans=KMeans(n_clusters=300, random_state=0).fit(cluster_centroides[['x','y']])
cluster_centroides['labels']=kmeans.labels_

**Clustering basado en densidad**

  Preparamos Dataset

In [ ]:
cluster_densidad=df_subset.copy()

**Predecimos la clase usando clustering**

https://scikit-learn.org/stable/modules/generated/sklearn.cluster.OPTICS.html

In [ ]:
from sklearn.cluster import OPTICS

In [ ]:
db= OPTICS(min_samples=20).fit(cluster_densidad[['x','y']])
cluster_densidad['labels']=db.labels_
cluster_densidad = cluster_densidad.sort_values(by ='labels')

In [ ]:
cluster_densidad.dtypes

x         float32
y         float32
labels      int64
dtype: object

## *Visualizar los clusters*

Visualización del cluster basado en centroides

In [ ]:
cluster_centroides.dtypes

x         float32
y         float32
labels      int32
dtype: object

In [ ]:
alt.Chart(cluster_centroides).mark_circle(size=10).encode(
    x=alt.X('x:Q',title='Eje x'),
    y=alt.Y('y:Q',title='Eje y'),
    color="labels:N",
    tooltip="labels"
).interactive()


alt.Chart(...)

Visualización de cluster basado en densidad

In [ ]:
alt.Chart(cluster_densidad).mark_circle(size=10).encode(
    x=alt.X('x:Q',title='Eje x'),
    y=alt.Y('y:Q',title='Eje y'),
    color="labels:N",
    tooltip="labels"
).interactive()


alt.Chart(...)

Se aprecia que hay muchos datos clasificados como "ruido" (label = -1), que no se pueden agrupar dentro de los clusters convencionales. Estos probablemente sean aquellos juegos que han tenido malas ventas, o que han sido publicados por editoras pequeñas, que no han lanzado muchos juegos al mercado, lo que dificulta la tarea de agruparlos. Además, analizando ambos gráficos, se verifica que algunos clusters se han podido identificar correctamente tanto en clustering basado en centroides como en clustering basado en densidad.

# Parte 4: Informe

##Pregunta 1

### ¿Eliminaste columnas en el dataset que no aportaban información? De ser así, ¿cuáles fueron y por qué? ¿Cómo resolviste el tema de los valores nulos?

-Para ambos casos eliminamos las columnas 'Id', 'Year' y 'Difficulty'.
El Id lo eliminamos ya que no tiene ninguna relación con alguna información sobre los videojuegos.
El año porque en general se venden grandes cantidades de videojuegos todos los años y por todas las editoras, por lo que no nos sirve para predecir ninguna de las dos clases.
Por último, la dificultad porque en general todas las editoras tienen juegos con muchas dificultades distintas y esta información no es una herramienta fundamental para predecir cuantas ventas se lograron tampoco.

-Para los valores nulos primero revisamos cuantos valores habían en cada columna (a excepción de las tres eliminadas).
El atributo 'Ign_score' por la gran cantidad de valores nulos que tenía decidimos borrarlo en ambos casos ya que aportaba con poca información. 'NA_Sales', 'EU_Sales', 'JP_Sales' y 'Other_Sales' por no tener una gran cantidad de valores nulos y ser columnas con valores númericos, decidimos reemplazar los valores nulos con el promedio de los valores de cada uno.
Para los atributos 'Name', 'Genre', 'Publisher' y 'Platform' que también tenian pocos valores nulos por ser valores no númericos decidimos eliminar las filas en donde los valores de estos atributos fueran nulos.

(No pudimos resumir mas nuestra respuesta)

##Pregunta 2

### ¿Qué normalizaste, filas o columnas? ¿Por qué? ¿Para qué sirve normalizar los datos?

Normalizamos las columnas mediante MinMaxScaler. Escogimos normalizar las columnas porque nos interesaba que las features estuviesen normalizadas independientemente unas de otras, para que así la información del dataset se mantuviera intacta y se pudiera visualizar la diferencia o relación entre los valores de cada atributo. Normalizar es importante porque, al usar algoritmos de machine learning, necesitamos que no se le de más peso a una feature por tener valores numéricos más grandes. Normalizar soluciona este problema al dejar todos los valores entre 0 y 1.

##Pregunta 3

### ¿Por qué se separan los datos en set de entrenamiento y set de pruebas? ¿Qué proporción de los datos utilizaste para cada uno y por qué?

El set de entrenamiento nos sirve, por decirlo de alguna manera, para nutrir de conocimiento a nuestro modelo, ya que lo nutrimos de datos. Una vez entrenado, obtenemos predicciones a partir de X_test, las que luego comparamos con los valores de prueba almacenados en y_test. Ya con todos estos datos podemos calcular las métricas de eficacia del modelo, determinando así si tuvimos éxito o no en la construccion de este.  Utilizamos para el primer caso 30,01% y en el segundo 50% de los datos para testear, modificando además el "random state" de este último, a 3 --  Lo que esto hace es variar la distribución de las filas del dataset en los sets de entrenamiento y prueba. Para ambos casos, probamos con varias proporciones, siendo las indicadas las que nos dieron mejores resultados a la hora de evaluar los modelos.

##Pregunta 4

### ¿Qué hiperparámetros modificaste para probar tu clasificador? ¿Y el regresor? ¿Cuáles combinaciones de parámetros te dieron mejores resultados y por qué crees que es así?

Para el clasificador en sí, modificamos el hiperparámetro n_neighbors, fijándolo en 23. Además de eso, modificamos el hiperparámetro weight a distnace, lo que posibilitó que los vecinos más cercanos de un punto de consulta tuviesen una mayor influencia que los vecinos que están más lejos, subiendo la accuracy del modelo. Con respecto al hiperparámetro "algorithm", lo dejamos en modo automático, para que los vecinos cercanos se calculen de manera adecuada en función de los valores pasados al fit. Para el regresor, dejamos todos los hiperparámetros en los valores default, ya que nos enfocamos en variar las configuraciones de los sets de entrenamiento y pruebas.  Con respecto al motivo por el que estas combinaciones nos dieron mejores resultados, nos parece difícil de decir a ciencia cierta, pero creemos que, por ejemplo, fijar un numero relativamente alto de n_neighbors (en comparacion con los ejemplos que encontramos que usualmente fijaban n_neighbors a 3) se justifica ya que tenemos un dataset bastante grande, con sobre 16000 filas de datos.

(No pudimos resumir más la respuesta)


##Pregunta 5

### Para el clasificador, explica la diferencia entre las métricas del set de pruebas para cada clase, ¿Qué nos dice de la calidad del clasificador por cada clase?. Justifica.

Las diferencias al predecir con el modelo del test de entrenamiento y el de testeo fueron considerablemente grandes ya que en el modelo del test de testeo los valores son sumamente pequeños (un valor de accuracy, recall, precision y f1-score  bajos ). En cambio en el modelo de entrenamiento claramente observamos un rendimiento perfecto ya que predice los datos que le dimos originalmente para entrenar a nuestro modelo. Esto nos dice que la calidad del rendimiento no es ideal ya que nuestros valores de rendimiento fueron sumamente bajos.

##Pregunta 6

### Al usar t-SNE reducimos la dimensionalidad de los datos. Nombra dos razones para hacer eso.

1. Es mas sencillo visualizar los datos en 2D y ver las relaciones que tienen entre ellos
2. Minimiza el tiempo usado para la ejecución y analisis y el amacenamiento usado.

##Pregunta 7

### ¿Cuantos centroides elegiste para la división del set de datos? Justifica.

Para determinar el numero de centroides utilizamos una métrica denominada silhouette score, de sklearn. Esta métrica entrega valores entre -1 y 1. El número de centroides a utilizar será aquel que entregue una silhouette score más cercana a 1. En nuestro caso fueron 300 clusters, que al determinar la métrica silhouette score nos dio un valor sobre 0.4

##Pregunta 8

### ¿Que observaste al graficar los puntos luego de reducir su dimensionalidad? ¿Servirá hacer clustering para este set de datos?

Al reducir la dimensionalidad, se ve un gráfico en el que los datos tienden a estar muy condensados, creando una figura que pareciera tener algunas zonas delimitadas, siendo díficil concluir algo a simple vista. Creemos que estas zonas delimitadas podrían representar clusters, pero no nos es posible asegurarlo solo observando al grafico por lo que es necesario hacer clustering para poder visualizarlos.

#Bonus


https://scikit-learn.org/stable/modules/svm.html#svm-classification

Clasificador svm

In [ ]:
from sklearn import svm
clf = svm.SVC()
clf.fit(X_train, y_train)

/usr/local/lib/python3.6/dist-packages/sklearn/utils/validation.py:760: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


SVC(C=1.0, break_ties=False, cache_size=200, class_weight=None, coef0=0.0,
    decision_function_shape='ovr', degree=3, gamma='scale', kernel='rbf',
    max_iter=-1, probability=False, random_state=None, shrinking=True,
    tol=0.001, verbose=False)

In [ ]:
ysvm_pred=clf.predict(X_test)

Viendo los valores del accuracy, vemos como el clasificador KNN usado originalmente funciona mejor que el SVM para predecir la editora

In [ ]:
print(accuracy_score(y_test, (ysvm_pred)))

0.15612409347300565


In [ ]:
print(accuracy_score(y_test, (y_pred)))

0.24153908138597904


https://scikit-learn.org/stable/modules/neighbors.html#nearest-neighbors-regression

Regresor KNN

In [ ]:
from sklearn import neighbors

In [ ]:
knn = neighbors.KNeighborsRegressor(n_neighbors=3)

In [ ]:
knn.fit(X2, y2)

In [ ]:
y2_predknn = knn.predict(X2_test)

NotFittedError: ignored

Viendo los valores del 'Mean squared error', vemos como el clasificador KNN nos da un mayor error que el método de regresión lineal usado originalmente para predecir las ventas en el resto del mundo

In [ ]:
print('Mean squared error: %.2f'
      % mean_squared_error(y2_test, y2_predknn))

Mean squared error: 0.04


In [ ]:
print('Mean squared error: %.2f'
      % mean_squared_error(y2_test, y2_pred))

Mean squared error: 0.01
